## Overview of the Bengali Grepheme Images

In [1]:
import os
from tqdm.auto import tqdm
import pandas as pd
import numpy as np
import PIL.Image as Image, PIL.ImageDraw as ImageDraw, PIL.ImageFont as ImageFont
import time, sys
import seaborn as sns
import matplotlib.pyplot as plt
from tqdm import tqdm_notebook
%matplotlib inline

sys.path.append("../tools/")
from helpers import *
# (get_n, get_dummies, resize, image_from_char, 
#                      plot_count, display_image_from_data,
#                     display_writting_variety, crop_resize)

In [2]:
import torch
import torch.nn as nn
import torch.optim as optim
import torchvision
import torch.utils.model_zoo as model_zoo
from torch.optim import lr_scheduler
from torchvision import datasets, models, transforms
from torch.utils.data import Dataset, DataLoader

In [3]:
for dirname, _, filenames in os.walk('../../data'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

../../data/test_image_data_3.parquet
../../data/train.csv
../../data/test_image_data_1.parquet
../../data/train_image_data_2.parquet
../../data/train_image_data_3.parquet
../../data/test_image_data_2.parquet
../../data/test_image_data_0.parquet
../../data/train_image_data_0.parquet
../../data/class_map.csv
../../data/test.csv
../../data/train_image_data_1.parquet
../../data/sample_submission.csv
../../data/Kalpurush_Fonts/kalpurush-2.ttf


### Trainingset 

In [4]:
### training dataframe
DATA_FOLDER = '../../data'
train_df = pd.read_csv(os.path.join(DATA_FOLDER, 'train.csv'))
print(train_df.shape)
train_df.head()

(200840, 5)


image_id  grapheme_root  vowel_diacritic  consonant_diacritic grapheme
0  Train_0             15                9                    5   ক্ট্রো
1  Train_1            159                0                    0        হ
2  Train_2             22                3                    5     খ্রী
3  Train_3             53                2                    2     র্টি
4  Train_4             71                9                    5     থ্রো

### Testingset

In [5]:
### Testing dataframe
test_df = pd.read_csv(os.path.join(DATA_FOLDER, 'test.csv'))
print(test_df.shape)
test_df.head()

(36, 3)


row_id image_id            component
0  Test_0_consonant_diacritic   Test_0  consonant_diacritic
1        Test_0_grapheme_root   Test_0        grapheme_root
2      Test_0_vowel_diacritic   Test_0      vowel_diacritic
3  Test_1_consonant_diacritic   Test_1  consonant_diacritic
4        Test_1_grapheme_root   Test_1        grapheme_root

### Class map

In [6]:
### Classes for three components
class_map_df = pd.read_csv(os.path.join(DATA_FOLDER, 'class_map.csv'))
print(class_map_df.shape)
class_map_df.head()

(186, 3)


component_type  label component
0  grapheme_root      0         ং
1  grapheme_root      1         ঃ
2  grapheme_root      2         অ
3  grapheme_root      3         আ
4  grapheme_root      4         ই

### Submission format

In [7]:
### Example of submission format
sample_submission_df = pd.read_csv(os.path.join(DATA_FOLDER, 'sample_submission.csv'))
sample_submission_df.head()

row_id  target
0  Test_0_consonant_diacritic       0
1        Test_0_grapheme_root       0
2      Test_0_vowel_diacritic       0
3  Test_1_consonant_diacritic       0
4        Test_1_grapheme_root       0

### Image pixels

In [8]:
train_0_df = pd.read_parquet(os.path.join(DATA_FOLDER,'train_image_data_1.parquet'))
print(train_0_df.shape)
train_0_df.head()

(50210, 32333)


image_id    0    1    2    3    4    5    6    7    8  ...  32322  \
0  Train_50210  246  253  251  250  249  252  246  250  250  ...    255   
1  Train_50211  250  245  241  244  249  253  253  254  254  ...    254   
2  Train_50212  248  248  249  249  250  251  250  250  249  ...    255   
3  Train_50213  253  252  250  252  252  251  252  252  252  ...    252   
4  Train_50214  250  252  252  250  250  252  253  254  254  ...    251   

   32323  32324  32325  32326  32327  32328  32329  32330  32331  
0    255    255    255    255    255    255    255    254    253  
1    254    253    253    253    254    255    253    253    254  
2    255    255    255    255    255    255    255    255    255  
3    252    253    252    252    251    250    251    251    253  
4    252    251    250    251    252    252    252    252    252  

[5 rows x 32333 columns]

In [9]:
import cv2
simple_transform_valid = transforms.Compose([
    transforms.ToTensor(),
    torchtransforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
])

In [10]:
def bbox(img):
    rows = np.any(img, axis=1)
    cols = np.any(img, axis=0)
    rmin, rmax = np.where(rows)[0][[0, -1]]
    cmin, cmax = np.where(cols)[0][[0, -1]]
    return rmin, rmax, cmin, cmax
def crop_resize(img0, size=128, pad=16):
    HEIGHT = 137
    WIDTH = 236
    #crop a box around pixels large than the threshold
    #some images contain line at the sides
    ymin,ymax,xmin,xmax = bbox(img0[5:-5,5:-5] > 80)
    #cropping may cut too much, so we need to add it back
    xmin = xmin - 13 if (xmin > 13) else 0
    ymin = ymin - 10 if (ymin > 10) else 0
    xmax = xmax + 13 if (xmax < WIDTH - 13) else WIDTH
    ymax = ymax + 10 if (ymax < HEIGHT - 10) else HEIGHT
    img = img0[ymin:ymax,xmin:xmax]
    #remove low intensity pixels as noise
    img[img < 28] = 0
    lx, ly = xmax-xmin,ymax-ymin
    l = max(lx,ly) + pad
    #make sure that the aspect ratio is kept in rescaling
    img = np.pad(img, [((l-ly)//2,), ((l-lx)//2,)], mode='constant')
    return cv2.resize(img,(size,size))
class ClsTestDataset(Dataset):
    def __init__(self, df, torchtransforms):
        self.df = df
        self.pathes = self.df.iloc[:,0].values
        self.data = self.df.iloc[:, 1:].values
        self.torchtransforms = torchtransforms

    def __getitem__(self, idx):
        HEIGHT = 137
        WIDTH = 236
        #row = self.df.iloc[idx].values
        path = self.pathes[idx]
        img = self.data[idx, :]
        img = 255 - img.reshape(HEIGHT, WIDTH).astype(np.uint8)
        #img = crop_resize(img, size=128)
        img = cv2.cvtColor(img, cv2.COLOR_GRAY2BGR)       
        img = transforms.ToPILImage()(img)
        img = self.torchtransforms(img)
        return path, img
    def __len__(self):
        return len(self.df)

def make_loader(
        data_folder,
        batch_size=64,
        num_workers=2,
        is_shuffle=False,
):

    image_dataset = ClsTestDataset(df = data_folder,
                                    torchtransforms = simple_transform_valid)

    return DataLoader(
    image_dataset,
    batch_size=batch_size,
    num_workers=num_workers,
    pin_memory=True,
    shuffle=is_shuffle
    )

In [11]:
train_loader = make_loader(data_folder=train_0_df, 
                           batch_size=64,
                           num_workers=8,
                           is_shuffle=False)
# in pytorch, the image batch come in with shape [batch_size, channel, width, height]
mean = 0
mean2 = 0
size = 0
for _, img_batch in tqdm(train_loader):
    print(img_batch)
    mean += img_batch.mean([2,3]).sum(0)
    mean2 += img_batch.pow(2).mean([2,3]).sum(0)
    size += img_batch.size()[0]
mean = mean / size
var = torch.sqrt(mean2 / size - mean.pow(2))
print(mean, var)

tensor([[[[0.0353, 0.0078, 0.0157,  ..., 0.0039, 0.0039, 0.0039],
          [0.0471, 0.0078, 0.0118,  ..., 0.0000, 0.0000, 0.0000],
          [0.0314, 0.0157, 0.0118,  ..., 0.0000, 0.0000, 0.0000],
          ...,
          [0.0078, 0.0039, 0.0000,  ..., 0.0000, 0.0039, 0.0078],
          [0.0118, 0.0078, 0.0000,  ..., 0.0000, 0.0039, 0.0078],
          [0.0039, 0.0078, 0.0000,  ..., 0.0000, 0.0039, 0.0078]],

         [[0.0353, 0.0078, 0.0157,  ..., 0.0039, 0.0039, 0.0039],
          [0.0471, 0.0078, 0.0118,  ..., 0.0000, 0.0000, 0.0000],
          [0.0314, 0.0157, 0.0118,  ..., 0.0000, 0.0000, 0.0000],
          ...,
          [0.0078, 0.0039, 0.0000,  ..., 0.0000, 0.0039, 0.0078],
          [0.0118, 0.0078, 0.0000,  ..., 0.0000, 0.0039, 0.0078],
          [0.0039, 0.0078, 0.0000,  ..., 0.0000, 0.0039, 0.0078]],

         [[0.0353, 0.0078, 0.0157,  ..., 0.0039, 0.0039, 0.0039],
          [0.0471, 0.0078, 0.0118,  ..., 0.0000, 0.0000, 0.0000],
          [0.0314, 0.0157, 0.0118,  ..., 0

tensor([[[[0.0157, 0.0235, 0.0157,  ..., 0.0235, 0.0157, 0.0078],
          [0.0275, 0.0471, 0.0471,  ..., 0.0118, 0.0078, 0.0078],
          [0.0157, 0.0078, 0.0078,  ..., 0.0000, 0.0039, 0.0118],
          ...,
          [0.0000, 0.0000, 0.0000,  ..., 0.0078, 0.0078, 0.0078],
          [0.0000, 0.0000, 0.0000,  ..., 0.0039, 0.0039, 0.0039],
          [0.0000, 0.0000, 0.0000,  ..., 0.0078, 0.0078, 0.0078]],

         [[0.0157, 0.0235, 0.0157,  ..., 0.0235, 0.0157, 0.0078],
          [0.0275, 0.0471, 0.0471,  ..., 0.0118, 0.0078, 0.0078],
          [0.0157, 0.0078, 0.0078,  ..., 0.0000, 0.0039, 0.0118],
          ...,
          [0.0000, 0.0000, 0.0000,  ..., 0.0078, 0.0078, 0.0078],
          [0.0000, 0.0000, 0.0000,  ..., 0.0039, 0.0039, 0.0039],
          [0.0000, 0.0000, 0.0000,  ..., 0.0078, 0.0078, 0.0078]],

         [[0.0157, 0.0235, 0.0157,  ..., 0.0235, 0.0157, 0.0078],
          [0.0275, 0.0471, 0.0471,  ..., 0.0118, 0.0078, 0.0078],
          [0.0157, 0.0078, 0.0078,  ..., 0

tensor([[[[0.0157, 0.0431, 0.0745,  ..., 0.0039, 0.0039, 0.0039],
          [0.0353, 0.0431, 0.0431,  ..., 0.0039, 0.0039, 0.0039],
          [0.0353, 0.0235, 0.0314,  ..., 0.0000, 0.0000, 0.0000],
          ...,
          [0.0000, 0.0000, 0.0000,  ..., 0.0275, 0.0078, 0.0275],
          [0.0039, 0.0000, 0.0039,  ..., 0.0157, 0.0039, 0.0235],
          [0.0039, 0.0039, 0.0039,  ..., 0.0196, 0.0039, 0.0353]],

         [[0.0157, 0.0431, 0.0745,  ..., 0.0039, 0.0039, 0.0039],
          [0.0353, 0.0431, 0.0431,  ..., 0.0039, 0.0039, 0.0039],
          [0.0353, 0.0235, 0.0314,  ..., 0.0000, 0.0000, 0.0000],
          ...,
          [0.0000, 0.0000, 0.0000,  ..., 0.0275, 0.0078, 0.0275],
          [0.0039, 0.0000, 0.0039,  ..., 0.0157, 0.0039, 0.0235],
          [0.0039, 0.0039, 0.0039,  ..., 0.0196, 0.0039, 0.0353]],

         [[0.0157, 0.0431, 0.0745,  ..., 0.0039, 0.0039, 0.0039],
          [0.0353, 0.0431, 0.0431,  ..., 0.0039, 0.0039, 0.0039],
          [0.0353, 0.0235, 0.0314,  ..., 0

tensor([[[[0.0196, 0.0157, 0.0118,  ..., 0.0000, 0.0000, 0.0000],
          [0.0118, 0.0078, 0.0039,  ..., 0.0000, 0.0000, 0.0000],
          [0.0039, 0.0039, 0.0039,  ..., 0.0000, 0.0000, 0.0000],
          ...,
          [0.0078, 0.0078, 0.0078,  ..., 0.0000, 0.0078, 0.0235],
          [0.0078, 0.0078, 0.0078,  ..., 0.0039, 0.0118, 0.0275],
          [0.0078, 0.0078, 0.0078,  ..., 0.0000, 0.0078, 0.0235]],

         [[0.0196, 0.0157, 0.0118,  ..., 0.0000, 0.0000, 0.0000],
          [0.0118, 0.0078, 0.0039,  ..., 0.0000, 0.0000, 0.0000],
          [0.0039, 0.0039, 0.0039,  ..., 0.0000, 0.0000, 0.0000],
          ...,
          [0.0078, 0.0078, 0.0078,  ..., 0.0000, 0.0078, 0.0235],
          [0.0078, 0.0078, 0.0078,  ..., 0.0039, 0.0118, 0.0275],
          [0.0078, 0.0078, 0.0078,  ..., 0.0000, 0.0078, 0.0235]],

         [[0.0196, 0.0157, 0.0118,  ..., 0.0000, 0.0000, 0.0000],
          [0.0118, 0.0078, 0.0039,  ..., 0.0000, 0.0000, 0.0000],
          [0.0039, 0.0039, 0.0039,  ..., 0

tensor([[[[0.0549, 0.0549, 0.0510,  ..., 0.0784, 0.0745, 0.0784],
          [0.0314, 0.0275, 0.0235,  ..., 0.0235, 0.0196, 0.0196],
          [0.0118, 0.0118, 0.0196,  ..., 0.0157, 0.0157, 0.0196],
          ...,
          [0.0157, 0.0039, 0.0078,  ..., 0.0157, 0.0118, 0.0078],
          [0.0157, 0.0039, 0.0118,  ..., 0.0118, 0.0078, 0.0039],
          [0.0078, 0.0039, 0.0078,  ..., 0.0118, 0.0078, 0.0039]],

         [[0.0549, 0.0549, 0.0510,  ..., 0.0784, 0.0745, 0.0784],
          [0.0314, 0.0275, 0.0235,  ..., 0.0235, 0.0196, 0.0196],
          [0.0118, 0.0118, 0.0196,  ..., 0.0157, 0.0157, 0.0196],
          ...,
          [0.0157, 0.0039, 0.0078,  ..., 0.0157, 0.0118, 0.0078],
          [0.0157, 0.0039, 0.0118,  ..., 0.0118, 0.0078, 0.0039],
          [0.0078, 0.0039, 0.0078,  ..., 0.0118, 0.0078, 0.0039]],

         [[0.0549, 0.0549, 0.0510,  ..., 0.0784, 0.0745, 0.0784],
          [0.0314, 0.0275, 0.0235,  ..., 0.0235, 0.0196, 0.0196],
          [0.0118, 0.0118, 0.0196,  ..., 0

...

tensor([[[[0.0000, 0.0000, 0.0000,  ..., 0.0196, 0.0157, 0.0157],
          [0.0000, 0.0000, 0.0000,  ..., 0.0157, 0.0157, 0.0157],
          [0.0000, 0.0000, 0.0000,  ..., 0.0078, 0.0078, 0.0118],
          ...,
          [0.0118, 0.0078, 0.0039,  ..., 0.0000, 0.0000, 0.0000],
          [0.0275, 0.0118, 0.0078,  ..., 0.0000, 0.0000, 0.0000],
          [0.0275, 0.0157, 0.0078,  ..., 0.0000, 0.0000, 0.0000]],

         [[0.0000, 0.0000, 0.0000,  ..., 0.0196, 0.0157, 0.0157],
          [0.0000, 0.0000, 0.0000,  ..., 0.0157, 0.0157, 0.0157],
          [0.0000, 0.0000, 0.0000,  ..., 0.0078, 0.0078, 0.0118],
          ...,
          [0.0118, 0.0078, 0.0039,  ..., 0.0000, 0.0000, 0.0000],
          [0.0275, 0.0118, 0.0078,  ..., 0.0000, 0.0000, 0.0000],
          [0.0275, 0.0157, 0.0078,  ..., 0.0000, 0.0000, 0.0000]],

         [[0.0000, 0.0000, 0.0000,  ..., 0.0196, 0.0157, 0.0157],
          [0.0000, 0.0000, 0.0000,  ..., 0.0157, 0.0157, 0.0157],
          [0.0000, 0.0000, 0.0000,  ..., 0

tensor([[[[0.0078, 0.0078, 0.0078,  ..., 0.0078, 0.0078, 0.0078],
          [0.0039, 0.0039, 0.0039,  ..., 0.0078, 0.0078, 0.0118],
          [0.0039, 0.0039, 0.0039,  ..., 0.0118, 0.0078, 0.0118],
          ...,
          [0.0078, 0.0039, 0.0039,  ..., 0.0118, 0.0118, 0.0078],
          [0.0039, 0.0000, 0.0000,  ..., 0.0078, 0.0078, 0.0039],
          [0.0000, 0.0000, 0.0000,  ..., 0.0118, 0.0118, 0.0078]],

         [[0.0078, 0.0078, 0.0078,  ..., 0.0078, 0.0078, 0.0078],
          [0.0039, 0.0039, 0.0039,  ..., 0.0078, 0.0078, 0.0118],
          [0.0039, 0.0039, 0.0039,  ..., 0.0118, 0.0078, 0.0118],
          ...,
          [0.0078, 0.0039, 0.0039,  ..., 0.0118, 0.0118, 0.0078],
          [0.0039, 0.0000, 0.0000,  ..., 0.0078, 0.0078, 0.0039],
          [0.0000, 0.0000, 0.0000,  ..., 0.0118, 0.0118, 0.0078]],

         [[0.0078, 0.0078, 0.0078,  ..., 0.0078, 0.0078, 0.0078],
          [0.0039, 0.0039, 0.0039,  ..., 0.0078, 0.0078, 0.0118],
          [0.0039, 0.0039, 0.0039,  ..., 0

tensor([[[[0.0118, 0.0078, 0.0078,  ..., 0.0157, 0.0196, 0.0118],
          [0.0078, 0.0078, 0.0039,  ..., 0.0078, 0.0157, 0.0118],
          [0.0078, 0.0078, 0.0078,  ..., 0.0118, 0.0196, 0.0157],
          ...,
          [0.0392, 0.0314, 0.0157,  ..., 0.0314, 0.0314, 0.0353],
          [0.0431, 0.0314, 0.0118,  ..., 0.0275, 0.0275, 0.0235],
          [0.0314, 0.0235, 0.0118,  ..., 0.0118, 0.0118, 0.0118]],

         [[0.0118, 0.0078, 0.0078,  ..., 0.0157, 0.0196, 0.0118],
          [0.0078, 0.0078, 0.0039,  ..., 0.0078, 0.0157, 0.0118],
          [0.0078, 0.0078, 0.0078,  ..., 0.0118, 0.0196, 0.0157],
          ...,
          [0.0392, 0.0314, 0.0157,  ..., 0.0314, 0.0314, 0.0353],
          [0.0431, 0.0314, 0.0118,  ..., 0.0275, 0.0275, 0.0235],
          [0.0314, 0.0235, 0.0118,  ..., 0.0118, 0.0118, 0.0118]],

         [[0.0118, 0.0078, 0.0078,  ..., 0.0157, 0.0196, 0.0118],
          [0.0078, 0.0078, 0.0039,  ..., 0.0078, 0.0157, 0.0118],
          [0.0078, 0.0078, 0.0078,  ..., 0

tensor([[[[0.0078, 0.0118, 0.0196,  ..., 0.0431, 0.0431, 0.0471],
          [0.0078, 0.0118, 0.0078,  ..., 0.0235, 0.0235, 0.0196],
          [0.0118, 0.0157, 0.0078,  ..., 0.0078, 0.0078, 0.0078],
          ...,
          [0.0157, 0.0157, 0.0118,  ..., 0.0157, 0.0196, 0.0196],
          [0.0118, 0.0118, 0.0078,  ..., 0.0078, 0.0118, 0.0157],
          [0.0118, 0.0118, 0.0078,  ..., 0.0078, 0.0157, 0.0196]],

         [[0.0078, 0.0118, 0.0196,  ..., 0.0431, 0.0431, 0.0471],
          [0.0078, 0.0118, 0.0078,  ..., 0.0235, 0.0235, 0.0196],
          [0.0118, 0.0157, 0.0078,  ..., 0.0078, 0.0078, 0.0078],
          ...,
          [0.0157, 0.0157, 0.0118,  ..., 0.0157, 0.0196, 0.0196],
          [0.0118, 0.0118, 0.0078,  ..., 0.0078, 0.0118, 0.0157],
          [0.0118, 0.0118, 0.0078,  ..., 0.0078, 0.0157, 0.0196]],

         [[0.0078, 0.0118, 0.0196,  ..., 0.0431, 0.0431, 0.0471],
          [0.0078, 0.0118, 0.0078,  ..., 0.0235, 0.0235, 0.0196],
          [0.0118, 0.0157, 0.0078,  ..., 0

tensor([[[[0.0118, 0.0118, 0.0118,  ..., 0.0039, 0.0039, 0.0039],
          [0.0078, 0.0118, 0.0118,  ..., 0.0039, 0.0039, 0.0039],
          [0.0078, 0.0078, 0.0118,  ..., 0.0078, 0.0078, 0.0078],
          ...,
          [0.0157, 0.0078, 0.0039,  ..., 0.0000, 0.0078, 0.0039],
          [0.0078, 0.0039, 0.0000,  ..., 0.0039, 0.0157, 0.0118],
          [0.0078, 0.0000, 0.0000,  ..., 0.0078, 0.0157, 0.0235]],

         [[0.0118, 0.0118, 0.0118,  ..., 0.0039, 0.0039, 0.0039],
          [0.0078, 0.0118, 0.0118,  ..., 0.0039, 0.0039, 0.0039],
          [0.0078, 0.0078, 0.0118,  ..., 0.0078, 0.0078, 0.0078],
          ...,
          [0.0157, 0.0078, 0.0039,  ..., 0.0000, 0.0078, 0.0039],
          [0.0078, 0.0039, 0.0000,  ..., 0.0039, 0.0157, 0.0118],
          [0.0078, 0.0000, 0.0000,  ..., 0.0078, 0.0157, 0.0235]],

         [[0.0118, 0.0118, 0.0118,  ..., 0.0039, 0.0039, 0.0039],
          [0.0078, 0.0118, 0.0118,  ..., 0.0039, 0.0039, 0.0039],
          [0.0078, 0.0078, 0.0118,  ..., 0

In [ ]:
pixels_train_0 = 255 - train_0_df.iloc[7, 1:].values

plt.hist(pixels_train_0[pixels_train_0 > 13], color='brown');

In [ ]:
plot_count('grapheme_root', 'grapheme_root (first most frequent 20 values - train)', train_df, size=4)

In [ ]:
plot_count('vowel_diacritic', 'vowel_diacritic (train)', train_df, size=3)

In [ ]:
plot_count('consonant_diacritic', 'consonant_diacritic (train)', train_df, size=2)

### Inspecting training images

In [ ]:
display_image_from_data(train_0_df.sample(25, random_state=42))

In [ ]:
display_writting_variety(train_0_df,train_df, class_map_df,
                         72,1,1,5)

#### Inspecting resized images

Compare the resize methods provided in the `oepncv` package and the resize method written by [lafoss](https://www.kaggle.com/iafoss/image-preprocessing-128x128)

#### Methods by lafoss

In [ ]:
HEIGHT = 137
WIDTH = 236
SIZE = 64

In [ ]:
n_imgs = 8
fig, axs = plt.subplots(2, n_imgs//2, figsize=(n_imgs*1.5, 6))

for idx in range(n_imgs):
    #somehow the original input is inverted
    img0 = 255 - train_0_df.iloc[idx, 1:].values.reshape(HEIGHT, WIDTH).astype(np.uint8)
    #normalize each image by its max val
    img = (img0*(255.0/img0.max())).astype(np.uint8)
    img = crop_resize(img, size=SIZE)

    axs[idx%2, idx//2].imshow(img)
    axs[idx%2, idx//2].set_title('Crop & resize')
    axs[idx%2, idx//2].axis('off')
plt.show()

In [ ]:
arrayvalues = img.reshape(-1)
plt.hist(arrayvalues[arrayvalues > 13], color='navy')

Resize methods combining data augmentation methods used in the package `albumentations` and the image processing methods in `opencv`

In [ ]:
train_df = train_df.drop(['grapheme'], axis=1, inplace=False)

In [ ]:
train_df_new = pd.merge(pd.read_parquet(DATA_FOLDER + f'/train_image_data_{0}.parquet')[:10], 
                    train_df, on='image_id').drop(['image_id'], axis=1)
train_df_new.head()

In [ ]:
fig, ax = plt.subplots(nrows=2, ncols=4, figsize=(12, 6))
count=0
for row in ax:
    for col in row:
        col.imshow(resize(train_df_new.drop(['grapheme_root', 'vowel_diacritic', 'consonant_diacritic'], axis=1).iloc[[count]], size=SIZE, 
                          plain=False, need_progress_bar=False)\
                   .values.reshape(-1).reshape(SIZE, SIZE).astype(np.float64))
        count += 1
plt.show()

In [ ]:
array_7 = 255 - resize(train_df_new.drop(['grapheme_root', 'vowel_diacritic', 'consonant_diacritic'], axis=1).iloc[[count]], 
       size=128, plain=False, need_progress_bar=False)
plt.hist(array_7[array_7 > 13], color='m')